In [1]:
from kiteconnect import KiteConnect
import pandas as pd
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.chrome.options import Options
from requests.exceptions import ConnectionError, Timeout, RequestException
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import json
import datetime
import logging
import re
from zerodha import Zerodha_Api
from nsepython import nse_eq, oi_chain_builder, nsefetch

In [ ]:
api_key = 'mpnneadoqfjdci2m'
client_id = 'CCC807'

In [ ]:
kite = KiteConnect(api_key=api_key)
chrome_options = webdriver.ChromeOptions()
chrome_options.add_experimental_option('detach', True)
driver = webdriver.Chrome(options=chrome_options)
driver.get(kite.login_url())

In [25]:
url = driver.current_url

In [26]:
pattern = r"request_token=([^&]+)"

match = re.search(pattern, url)
if match:
    request_token = match.group(1)
    print("Request token:", request_token)
else:
    print("Request token not found.")

Request token: XX8l0xmZ4SPonvyOQP4vb20DDHbBgd5Q


In [27]:
user = kite.generate_session(request_token, 'or3uo9myd18elkwiyzv986re7jle0jpb')
kite.set_access_token(user["access_token"])

In [19]:
url = "https://www.nseindia.com/api/master-quote"
payload = nsefetch(url)
payload

['AARTIIND',
 'ABB',
 'ABCAPITAL',
 'ABFRL',
 'ACC',
 'ADANIENSOL',
 'ADANIENT',
 'ADANIGREEN',
 'ADANIPORTS',
 'ALKEM',
 'AMBUJACEM',
 'ANGELONE',
 'APLAPOLLO',
 'APOLLOHOSP',
 'APOLLOTYRE',
 'ASHOKLEY',
 'ASIANPAINT',
 'ASTRAL',
 'ATGL',
 'AUBANK',
 'AUROPHARMA',
 'AXISBANK',
 'BAJAJ-AUTO',
 'BAJAJFINSV',
 'BAJFINANCE',
 'BALKRISIND',
 'BANDHANBNK',
 'BANKBARODA',
 'BANKINDIA',
 'BEL',
 'BHARATFORG',
 'BHARTIARTL',
 'BHEL',
 'BIOCON',
 'BOSCHLTD',
 'BPCL',
 'BRITANNIA',
 'BSE',
 'BSOFT',
 'CAMS',
 'CANBK',
 'CDSL',
 'CESC',
 'CGPOWER',
 'CHAMBLFERT',
 'CHOLAFIN',
 'CIPLA',
 'COALINDIA',
 'COFORGE',
 'COLPAL',
 'CONCOR',
 'CROMPTON',
 'CUMMINSIND',
 'CYIENT',
 'DABUR',
 'DALBHARAT',
 'DEEPAKNTR',
 'DELHIVERY',
 'DIVISLAB',
 'DIXON',
 'DLF',
 'DMART',
 'DRREDDY',
 'EICHERMOT',
 'ESCORTS',
 'ETERNAL',
 'EXIDEIND',
 'FEDERALBNK',
 'GAIL',
 'GLENMARK',
 'GMRAIRPORT',
 'GODREJCP',
 'GODREJPROP',
 'GRANULES',
 'GRASIM',
 'HAL',
 'HAVELLS',
 'HCLTECH',
 'HDFCAMC',
 'HDFCBANK',
 'HDFCLIFE',
 

In [20]:
# Get instrument tokens
instrument_dump = kite.instruments(exchange="NSE")
inst_df = pd.DataFrame(instrument_dump)
inst_df

instrument_token exchange_token      tradingsymbol               name  \
0               256265           1001           NIFTY 50           NIFTY 50   
1               256777           1003   NIFTY MIDCAP 100   NIFTY MIDCAP 100   
2               260105           1016         NIFTY BANK         NIFTY BANK   
3               260617           1018          NIFTY 100          NIFTY 100   
4               257033           1004  NIFTY DIV OPPS 50  NIFTY DIV OPPS 50   
...                ...            ...                ...                ...   
7760         193772801         756925              PRIMO    PRIMO CHEMICALS   
7761         193774081         756930      769TFSIL28-N0                      
7762         193789953         756992      755TPREL40-N0                      
7763         193790465         756994      727TCHFL28-N0                      
7764         193790977         756996        680NHB32-N0                      

      last_price expiry  strike  tick_size  lot_size instrument_type  segment  \
0            0.0            0.0       0.00         0              EQ  INDICES   
1            0.0            0.0       0.00         0              EQ  INDICES   
2            0.0            0.0       0.00         0              EQ  INDICES   
3            0.0            0.0       0.00         0              EQ  INDICES   
4            0.0            0.0       0.00         0              EQ  INDICES   
...          ...    ...     ...        ...       ...             ...      ...   
7760         0.0            0.0       0.01         1              EQ      NSE   
7761         0.0            0.0       0.01         1              EQ      NSE   
7762         0.0            0.0       0.01         1              EQ      NSE   
7763         0.0            0.0       0.01         1              EQ      NSE   
7764         0.0            0.0       0.01         1              EQ      NSE   

     exchange  
0         NSE  
1         NSE  
2         NSE  
3         NSE  
4         NSE  
...       ...  
7760      NSE  
7761      NSE  
7762      NSE  
7763      NSE  
7764      NSE  

[7765 rows x 12 columns]

In [21]:
def get_token(symbol):
    token = inst_df[inst_df.tradingsymbol == symbol].instrument_token.values[0]
    return token

tokens = [get_token(sym) for sym in payload]
tokens

[1793,
 3329,
 5533185,
 7707649,
 5633,
 2615553,
 6401,
 912129,
 3861249,
 2995969,
 325121,
 82945,
 6599681,
 40193,
 41729,
 54273,
 60417,
 3691009,
 1552897,
 5436929,
 70401,
 1510401,
 4267265,
 4268801,
 81153,
 85761,
 579329,
 1195009,
 1214721,
 98049,
 108033,
 2714625,
 112129,
 2911489,
 558337,
 134657,
 140033,
 5013761,
 1790465,
 87553,
 2763265,
 5420545,
 160769,
 194561,
 163073,
 175361,
 177665,
 5215745,
 2955009,
 3876097,
 1215745,
 4376065,
 486657,
 1471489,
 197633,
 2067201,
 5105409,
 2457345,
 2800641,
 5552641,
 3771393,
 5097729,
 225537,
 232961,
 245249,
 1304833,
 173057,
 261889,
 1207553,
 1895937,
 3463169,
 2585345,
 4576001,
 3039233,
 315393,
 589569,
 2513665,
 1850625,
 1086465,
 341249,
 119553,
 345089,
 5619457,
 348929,
 4592385,
 359937,
 356865,
 364545,
 5331201,
 1270529,
 5573121,
 4774913,
 3677697,
 2863105,
 56321,
 2883073,
 3023105,
 387073,
 3663105,
 2865921,
 1346049,
 7458561,
 408065,
 2010113,
 415745,
 3920129,
 34844

In [30]:
# Fetch real-time quotes
quotes = kite.quote(tokens)
quotes

{'1041153': {'instrument_token': 1041153,
  'timestamp': datetime.datetime(2025, 4, 29, 14, 3, 19),
  'last_trade_time': datetime.datetime(2025, 4, 29, 14, 3, 14),
  'last_price': 714.95,
  'last_quantity': 4,
  'buy_quantity': 194987,
  'sell_quantity': 219587,
  'volume': 1003868,
  'average_price': 718.53,
  'oi': 0,
  'oi_day_high': 0,
  'oi_day_low': 0,
  'net_change': 0,
  'lower_circuit_limit': 643.9,
  'upper_circuit_limit': 786.95,
  'ohlc': {'open': 715.45, 'high': 723.95, 'low': 711.8, 'close': 715.45},
  'depth': {'buy': [{'price': 714.8, 'quantity': 1, 'orders': 1},
    {'price': 714.75, 'quantity': 1, 'orders': 1},
    {'price': 714.7, 'quantity': 9, 'orders': 1},
    {'price': 714.65, 'quantity': 3, 'orders': 1},
    {'price': 714.6, 'quantity': 131, 'orders': 5}],
   'sell': [{'price': 714.95, 'quantity': 247, 'orders': 2},
    {'price': 715, 'quantity': 25, 'orders': 2},
    {'price': 715.05, 'quantity': 177, 'orders': 3},
    {'price': 715.1, 'quantity': 13, 'orders':

In [31]:
fno_inst = kite.instruments(exchange="NFO")
fno_df = pd.DataFrame(fno_inst)
fno_df

instrument_token exchange_token         tradingsymbol       name  \
0              14626050          57133         NIFTY25MAYFUT      NIFTY   
1              14536962          56785         NIFTY25JUNFUT      NIFTY   
2              13623298          53216         NIFTY25JULFUT      NIFTY   
3              14625282          57130     BANKNIFTY25MAYFUT  BANKNIFTY   
4              14536194          56782     BANKNIFTY25JUNFUT  BANKNIFTY   
...                 ...            ...                   ...        ...   
31289          34898946         136324   ZYDUSLIFE25JUL940PE  ZYDUSLIFE   
31290          34899202         136325   ZYDUSLIFE25JUL960CE  ZYDUSLIFE   
31291          34899458         136326   ZYDUSLIFE25JUL960PE  ZYDUSLIFE   
31292          34900226         136329  ZYDUSLIFE25JUL1000CE  ZYDUSLIFE   
31293          34903810         136343  ZYDUSLIFE25JUL1000PE  ZYDUSLIFE   

       last_price      expiry  strike  tick_size  lot_size instrument_type  \
0             0.0  2025-05-29     0.0       0.10        75             FUT   
1             0.0  2025-06-26     0.0       0.10        75             FUT   
2             0.0  2025-07-31     0.0       0.10        75             FUT   
3             0.0  2025-05-29     0.0       0.20        30             FUT   
4             0.0  2025-06-26     0.0       0.20        30             FUT   
...           ...         ...     ...        ...       ...             ...   
31289         0.0  2025-07-31   940.0       0.05       900              PE   
31290         0.0  2025-07-31   960.0       0.05       900              CE   
31291         0.0  2025-07-31   960.0       0.05       900              PE   
31292         0.0  2025-07-31  1000.0       0.05       900              CE   
31293         0.0  2025-07-31  1000.0       0.05       900              PE   

       segment exchange  
0      NFO-FUT      NFO  
1      NFO-FUT      NFO  
2      NFO-FUT      NFO  
3      NFO-FUT      NFO  
4      NFO-FUT      NFO  
...        ...      ...  
31289  NFO-OPT      NFO  
31290  NFO-OPT      NFO  
31291  NFO-OPT      NFO  
31292  NFO-OPT      NFO  
31293  NFO-OPT      NFO  

[31294 rows x 12 columns]

In [36]:
fno_df = fno_df[fno_df['instrument_type'].isin(['CE', 'PE'])]

In [39]:
today = pd.Timestamp.now().normalize()

options_df = fno_df[
    (pd.to_datetime(fno_df['expiry']) >= today) &
    (pd.to_datetime(fno_df['expiry']) < today + pd.Timedelta(days=60))
]

options_df

instrument_token exchange_token        tradingsymbol       name  \
653            13312002          52000    NIFTY2543024350CE      NIFTY   
654            13312258          52001    NIFTY2543024350PE      NIFTY   
655            13310466          51994    NIFTY2543024300CE      NIFTY   
656            13311746          51999    NIFTY2543024300PE      NIFTY   
657            13312514          52002    NIFTY2543024400CE      NIFTY   
...                 ...            ...                  ...        ...   
31263          37512962         146535  ZYDUSLIFE25JUN760PE  ZYDUSLIFE   
31264          37512194         146532  ZYDUSLIFE25JUN740CE  ZYDUSLIFE   
31265          37512450         146533  ZYDUSLIFE25JUN740PE  ZYDUSLIFE   
31266          37511682         146530  ZYDUSLIFE25JUN720CE  ZYDUSLIFE   
31267          37511938         146531  ZYDUSLIFE25JUN720PE  ZYDUSLIFE   

       last_price      expiry   strike  tick_size  lot_size instrument_type  \
653           0.0  2025-04-30  24350.0       0.05        75              CE   
654           0.0  2025-04-30  24350.0       0.05        75              PE   
655           0.0  2025-04-30  24300.0       0.05        75              CE   
656           0.0  2025-04-30  24300.0       0.05        75              PE   
657           0.0  2025-04-30  24400.0       0.05        75              CE   
...           ...         ...      ...        ...       ...             ...   
31263         0.0  2025-06-26    760.0       0.05       900              PE   
31264         0.0  2025-06-26    740.0       0.05       900              CE   
31265         0.0  2025-06-26    740.0       0.05       900              PE   
31266         0.0  2025-06-26    720.0       0.05       900              CE   
31267         0.0  2025-06-26    720.0       0.05       900              PE   

       segment exchange  
653    NFO-OPT      NFO  
654    NFO-OPT      NFO  
655    NFO-OPT      NFO  
656    NFO-OPT      NFO  
657    NFO-OPT      NFO  
...        ...      ...  
31263  NFO-OPT      NFO  
31264  NFO-OPT      NFO  
31265  NFO-OPT      NFO  
31266  NFO-OPT      NFO  
31267  NFO-OPT      NFO  

[24480 rows x 12 columns]

In [40]:
symbols = options_df['name'].unique()
symbols

array(['NIFTY', 'BANKNIFTY', 'AARTIIND', 'ABB', 'ABCAPITAL', 'ABFRL',
       'ACC', 'ADANIENSOL', 'ADANIENT', 'ADANIGREEN', 'ADANIPORTS',
       'ALKEM', 'AMBUJACEM', 'ANGELONE', 'APLAPOLLO', 'APOLLOHOSP',
       'APOLLOTYRE', 'ASHOKLEY', 'ASIANPAINT', 'ASTRAL', 'ATGL', 'AUBANK',
       'AUROPHARMA', 'AXISBANK', 'BAJAJ-AUTO', 'BAJAJFINSV', 'BAJFINANCE',
       'BALKRISIND', 'BANDHANBNK', 'BANKBARODA', 'BANKINDIA', 'BEL',
       'BHARATFORG', 'BHARTIARTL', 'BHEL', 'BIOCON', 'BOSCHLTD', 'BPCL',
       'BRITANNIA', 'BSE', 'BSOFT', 'CAMS', 'CANBK', 'CDSL', 'CESC',
       'CGPOWER', 'CHAMBLFERT', 'CHOLAFIN', 'CIPLA', 'COALINDIA',
       'COFORGE', 'COLPAL', 'CONCOR', 'CROMPTON', 'CUMMINSIND', 'CYIENT',
       'DABUR', 'DALBHARAT', 'DEEPAKNTR', 'DELHIVERY', 'DIVISLAB',
       'DIXON', 'DLF', 'DMART', 'DRREDDY', 'EICHERMOT', 'ESCORTS',
       'ETERNAL', 'EXIDEIND', 'FEDERALBNK', 'FINNIFTY', 'GAIL',
       'GLENMARK', 'GMRAIRPORT', 'GODREJCP', 'GODREJPROP', 'GRANULES',
       'GRASIM', 'HAL', 

In [42]:
strikes = options_df['strike'].unique()
symbols = options_df['name'].unique()
quote = kite.quote(f'NSE:{symbols[0]}')
cmp = quote[f'NSE:{symbols[0]}']['last_price']
# Sort strikes based on absolute distance from CMP
top_5_atm_strikes = sorted(strikes, key=lambda x: abs(x - cmp))[:5]
top_5_atm_strikes

KeyError: 'NSE:NIFTY'

In [43]:
symbols = options_df['name'].unique()
strikes = options_df[options_df['name'] == symbols[0]]['strike'].unique()
quote = kite.quote(f'NSE:{symbols[0]}')
cmp = 24345
# Sort strikes based on absolute distance from CMP
top_5_atm_strikes = sorted(strikes, key=lambda x: abs(x - cmp))[:5]
top_5_atm_strikes

[24350.0, 24300.0, 24400.0, 24250.0, 24450.0]

In [33]:
# Fetch CMP
def fetch_cmp(symbol):
    quote = kite.quote(f'NSE:{symbol}')
    return quote[f'NSE:{symbol}']['last_price']

atm_results = []

for symbol in payload:
    print(f"Processing: {symbol}")
    
    cmp = fetch_cmp(symbol)
    # Filter option contracts for the symbol (nearest expiry)
    options_df = fno_df[
        (fno_df['name'] == symbol) &
        (fno_df['instrument_type'].isin(['CE', 'PE'])) &
        (pd.to_datetime(fno_df['expiry']).dt.date >= pd.Timestamp.now().date())
    ]

    nearest_expiry = options_df['expiry'].min()
    options_df = options_df[options_df['expiry'] == nearest_expiry]

    strikes = options_df['strike'].unique()
    atm_strike = min(strikes, key=lambda x: abs(x - cmp))

    atm_ce_token = options_df[
        (options_df['strike'] == atm_strike) & (options_df['instrument_type'] == 'CE')
    ]['instrument_token'].values[0]

    atm_pe_token = options_df[
        (options_df['strike'] == atm_strike) & (options_df['instrument_type'] == 'PE')
    ]['instrument_token'].values[0]

    # Fetch quotes for ATM CE and PE
    quotes = kite.quote([atm_ce_token, atm_pe_token])

    atm_ce_oi = quotes[str(atm_ce_token)]['oi']
    atm_pe_oi = quotes[str(atm_pe_token)]['oi']

    atm_results.append({
        'Symbol': symbol,
        'ATM Strike': atm_strike,
        'ATM CE OI': atm_ce_oi,
        'ATM PE OI': atm_pe_oi,
        'Total ATM OI': atm_ce_oi + atm_pe_oi
    })

# Compile and Sort results
atm_oi_df = pd.DataFrame(atm_results)
atm_oi_df = atm_oi_df.sort_values('Total ATM OI', ascending=False).reset_index(drop=True)

print(atm_oi_df)

Processing: AARTIIND
Processing: ABB
Processing: ABCAPITAL
Processing: ABFRL
Processing: ACC
Processing: ADANIENSOL
Processing: ADANIENT
Processing: ADANIGREEN
Processing: ADANIPORTS
Processing: ALKEM
Processing: AMBUJACEM
Processing: ANGELONE
Processing: APLAPOLLO
Processing: APOLLOHOSP
Processing: APOLLOTYRE
Processing: ASHOKLEY
Processing: ASIANPAINT
Processing: ASTRAL
Processing: ATGL
Processing: AUBANK
Processing: AUROPHARMA
Processing: AXISBANK
Processing: BAJAJ-AUTO
Processing: BAJAJFINSV
Processing: BAJFINANCE
Processing: BALKRISIND
Processing: BANDHANBNK
Processing: BANKBARODA
Processing: BANKINDIA
Processing: BEL
Processing: BHARATFORG
Processing: BHARTIARTL
Processing: BHEL
Processing: BIOCON
Processing: BOSCHLTD
Processing: BPCL
Processing: BRITANNIA
Processing: BSE
Processing: BSOFT
Processing: CAMS
Processing: CANBK
Processing: CDSL
Processing: CESC
Processing: CGPOWER
Processing: CHAMBLFERT
Processing: CHOLAFIN
Processing: CIPLA
Processing: COALINDIA
Processing: COFORGE


IndexError: index 0 is out of bounds for axis 0 with size 0

In [34]:
# Compile and Sort results
atm_oi_df = pd.DataFrame(atm_results)
atm_oi_df = atm_oi_df.sort_values('Total ATM OI', ascending=False).reset_index(drop=True)

print(atm_oi_df)

         Symbol  ATM Strike  ATM CE OI  ATM PE OI  Total ATM OI
0          IDEA         7.0   94880000   92440000     187320000
1    MANAPPURAM       235.0    5952000    6582000      12534000
2    FEDERALBNK       205.0    7300000    2355000       9655000
3    IDFCFIRSTB        67.0    5220000    4267500       9487500
4          BHEL       230.0    4318125    3100125       7418250
..          ...         ...        ...        ...           ...
190  SUPREMEIND      3550.0       4375       2000          6375
191    BOSCHLTD     29000.0       5425        875          6300
192    SHREECEM     30000.0       1500       2425          3925
193     PAGEIND     45000.0        780       1575          2355
194         MRF    133000.0          0          0             0

[195 rows x 5 columns]


In [35]:
quotes

{'36573954': {'instrument_token': 36573954,
  'timestamp': datetime.datetime(2025, 4, 29, 14, 9, 11),
  'last_trade_time': datetime.datetime(2025, 4, 29, 14, 6, 46),
  'last_price': 15.5,
  'last_quantity': 1350,
  'buy_quantity': 525150,
  'sell_quantity': 522450,
  'volume': 1409400,
  'average_price': 17.71,
  'oi': 843750,
  'oi_day_high': 845100,
  'oi_day_low': 681750,
  'net_change': 0,
  'lower_circuit_limit': 0.05,
  'upper_circuit_limit': 36.5,
  'ohlc': {'open': 16.5, 'high': 20.5, 'low': 15.1, 'close': 16.5},
  'depth': {'buy': [{'price': 15.6, 'quantity': 2700, 'orders': 2},
    {'price': 15.55, 'quantity': 12150, 'orders': 7},
    {'price': 15.5, 'quantity': 6750, 'orders': 5},
    {'price': 15.45, 'quantity': 16200, 'orders': 6},
    {'price': 15.4, 'quantity': 8100, 'orders': 4}],
   'sell': [{'price': 15.75, 'quantity': 6750, 'orders': 5},
    {'price': 15.8, 'quantity': 13500, 'orders': 5},
    {'price': 15.85, 'quantity': 13500, 'orders': 5},
    {'price': 15.9, 'qua

### Testing zerodha.py

In [2]:
init_zerodha = Zerodha_Api(api_key='mpnneadoqfjdci2m' ,api_secret_key='or3uo9myd18elkwiyzv986re7jle0jpb', client_id='CCC807')

2025-05-01 15:14:09,011 - INFO - Request token extracted: Pa1UhBJtj3P0ey4KuhGyFVitTmiGoqEO
2025-05-01 15:14:12,894 - INFO - Session generated and access token set.


In [3]:
fno_inst = init_zerodha.kite.instruments(exchange="NFO")

In [4]:
fno_df = pd.DataFrame(fno_inst)
options_df = fno_df[fno_df['instrument_type'].isin(['CE', 'PE'])]
today = pd.Timestamp.now().normalize()
options_df = fno_df[
            (pd.to_datetime(fno_df['expiry']) > today) &
            (pd.to_datetime(fno_df['expiry']) < today + pd.Timedelta(days=60))
            ]

In [5]:
options_df = options_df[options_df['instrument_type'].isin(['CE', 'PE'])]

In [6]:
symbols = options_df['name'].unique()
symbols

array(['NIFTY', 'BANKNIFTY', 'AARTIIND', 'ABB', 'ABCAPITAL', 'ABFRL',
       'ACC', 'ADANIENSOL', 'ADANIENT', 'ADANIGREEN', 'ADANIPORTS',
       'ALKEM', 'AMBUJACEM', 'ANGELONE', 'APLAPOLLO', 'APOLLOHOSP',
       'APOLLOTYRE', 'ASHOKLEY', 'ASIANPAINT', 'ASTRAL', 'ATGL', 'AUBANK',
       'AUROPHARMA', 'AXISBANK', 'BAJAJ-AUTO', 'BAJAJFINSV', 'BAJFINANCE',
       'BALKRISIND', 'BANDHANBNK', 'BANKBARODA', 'BANKINDIA', 'BEL',
       'BHARATFORG', 'BHARTIARTL', 'BHEL', 'BIOCON', 'BOSCHLTD', 'BPCL',
       'BRITANNIA', 'BSE', 'BSOFT', 'CAMS', 'CANBK', 'CDSL', 'CESC',
       'CGPOWER', 'CHAMBLFERT', 'CHOLAFIN', 'CIPLA', 'COALINDIA',
       'COFORGE', 'COLPAL', 'CONCOR', 'CROMPTON', 'CUMMINSIND', 'CYIENT',
       'DABUR', 'DALBHARAT', 'DEEPAKNTR', 'DELHIVERY', 'DIVISLAB',
       'DIXON', 'DLF', 'DMART', 'DRREDDY', 'EICHERMOT', 'ESCORTS',
       'ETERNAL', 'EXIDEIND', 'FEDERALBNK', 'FINNIFTY', 'GAIL',
       'GLENMARK', 'GMRAIRPORT', 'GODREJCP', 'GODREJPROP', 'GRANULES',
       'GRASIM', 'HAL', 

In [7]:
options_df

instrument_token exchange_token        tradingsymbol       name  \
653             9882626          38604    NIFTY2550824350CE      NIFTY   
654             9882882          38605    NIFTY2550824350PE      NIFTY   
655             9882114          38602    NIFTY2550824300CE      NIFTY   
656             9882370          38603    NIFTY2550824300PE      NIFTY   
657             9883138          38606    NIFTY2550824400CE      NIFTY   
...                 ...            ...                  ...        ...   
32063          37512962         146535  ZYDUSLIFE25JUN760PE  ZYDUSLIFE   
32064          37512194         146532  ZYDUSLIFE25JUN740CE  ZYDUSLIFE   
32065          37512450         146533  ZYDUSLIFE25JUN740PE  ZYDUSLIFE   
32066          37511682         146530  ZYDUSLIFE25JUN720CE  ZYDUSLIFE   
32067          37511938         146531  ZYDUSLIFE25JUN720PE  ZYDUSLIFE   

       last_price      expiry   strike  tick_size  lot_size instrument_type  \
653           0.0  2025-05-08  24350.0       0.05        75              CE   
654           0.0  2025-05-08  24350.0       0.05        75              PE   
655           0.0  2025-05-08  24300.0       0.05        75              CE   
656           0.0  2025-05-08  24300.0       0.05        75              PE   
657           0.0  2025-05-08  24400.0       0.05        75              CE   
...           ...         ...      ...        ...       ...             ...   
32063         0.0  2025-06-26    760.0       0.05       900              PE   
32064         0.0  2025-06-26    740.0       0.05       900              CE   
32065         0.0  2025-06-26    740.0       0.05       900              PE   
32066         0.0  2025-06-26    720.0       0.05       900              CE   
32067         0.0  2025-06-26    720.0       0.05       900              PE   

       segment exchange  
653    NFO-OPT      NFO  
654    NFO-OPT      NFO  
655    NFO-OPT      NFO  
656    NFO-OPT      NFO  
657    NFO-OPT      NFO  
...        ...      ...  
32063  NFO-OPT      NFO  
32064  NFO-OPT      NFO  
32065  NFO-OPT      NFO  
32066  NFO-OPT      NFO  
32067  NFO-OPT      NFO  

[25079 rows x 12 columns]

In [8]:
import yfinance as yf

In [9]:
symbols = ['IDEA', 'YESBANK', 'RELIANCE', 'ADANIENT', 'MANAPPURAM']
symbols = [s+'.NS' for s in symbols]
symbols

['IDEA.NS', 'YESBANK.NS', 'RELIANCE.NS', 'ADANIENT.NS', 'MANAPPURAM.NS']

In [10]:
ticker = yf.Tickers(symbols)
close = ticker.download(period = '1d')['Close']

[*********************100%***********************]  5 of 5 completed


In [11]:
close[symbols[0]][0]

7.119999885559082

In [12]:
symbols = options_df['name'].unique()
symbols_dict = {}
for ticker in symbols:
    if ticker == 'NIFTY':
        symbols_dict[ticker] = '^NSEI'
    elif ticker == 'BANKNIFTY':
        symbols_dict[ticker] = '^NSEBANK'
    elif ticker == 'FINNIFTY':
        symbols_dict[ticker] = 'NIFTY_FIN_SERVICE.NS'
    elif ticker == 'MIDCPNIFTY':
        symbols_dict[ticker] = 'NIFTY_MIDCAP_100.NS'
    elif ticker == 'NIFTYNXT50':
        symbols_dict[ticker] = '^NSMIDCP'
    else:
        symbols_dict[ticker] = ticker + '.NS'
symbols_dict

{'NIFTY': '^NSEI',
 'BANKNIFTY': '^NSEBANK',
 'AARTIIND': 'AARTIIND.NS',
 'ABB': 'ABB.NS',
 'ABCAPITAL': 'ABCAPITAL.NS',
 'ABFRL': 'ABFRL.NS',
 'ACC': 'ACC.NS',
 'ADANIENSOL': 'ADANIENSOL.NS',
 'ADANIENT': 'ADANIENT.NS',
 'ADANIGREEN': 'ADANIGREEN.NS',
 'ADANIPORTS': 'ADANIPORTS.NS',
 'ALKEM': 'ALKEM.NS',
 'AMBUJACEM': 'AMBUJACEM.NS',
 'ANGELONE': 'ANGELONE.NS',
 'APLAPOLLO': 'APLAPOLLO.NS',
 'APOLLOHOSP': 'APOLLOHOSP.NS',
 'APOLLOTYRE': 'APOLLOTYRE.NS',
 'ASHOKLEY': 'ASHOKLEY.NS',
 'ASIANPAINT': 'ASIANPAINT.NS',
 'ASTRAL': 'ASTRAL.NS',
 'ATGL': 'ATGL.NS',
 'AUBANK': 'AUBANK.NS',
 'AUROPHARMA': 'AUROPHARMA.NS',
 'AXISBANK': 'AXISBANK.NS',
 'BAJAJ-AUTO': 'BAJAJ-AUTO.NS',
 'BAJAJFINSV': 'BAJAJFINSV.NS',
 'BAJFINANCE': 'BAJFINANCE.NS',
 'BALKRISIND': 'BALKRISIND.NS',
 'BANDHANBNK': 'BANDHANBNK.NS',
 'BANKBARODA': 'BANKBARODA.NS',
 'BANKINDIA': 'BANKINDIA.NS',
 'BEL': 'BEL.NS',
 'BHARATFORG': 'BHARATFORG.NS',
 'BHARTIARTL': 'BHARTIARTL.NS',
 'BHEL': 'BHEL.NS',
 'BIOCON': 'BIOCON.NS',
 'BOS

In [13]:
list(symbols_dict.values())

['^NSEI',
 '^NSEBANK',
 'AARTIIND.NS',
 'ABB.NS',
 'ABCAPITAL.NS',
 'ABFRL.NS',
 'ACC.NS',
 'ADANIENSOL.NS',
 'ADANIENT.NS',
 'ADANIGREEN.NS',
 'ADANIPORTS.NS',
 'ALKEM.NS',
 'AMBUJACEM.NS',
 'ANGELONE.NS',
 'APLAPOLLO.NS',
 'APOLLOHOSP.NS',
 'APOLLOTYRE.NS',
 'ASHOKLEY.NS',
 'ASIANPAINT.NS',
 'ASTRAL.NS',
 'ATGL.NS',
 'AUBANK.NS',
 'AUROPHARMA.NS',
 'AXISBANK.NS',
 'BAJAJ-AUTO.NS',
 'BAJAJFINSV.NS',
 'BAJFINANCE.NS',
 'BALKRISIND.NS',
 'BANDHANBNK.NS',
 'BANKBARODA.NS',
 'BANKINDIA.NS',
 'BEL.NS',
 'BHARATFORG.NS',
 'BHARTIARTL.NS',
 'BHEL.NS',
 'BIOCON.NS',
 'BOSCHLTD.NS',
 'BPCL.NS',
 'BRITANNIA.NS',
 'BSE.NS',
 'BSOFT.NS',
 'CAMS.NS',
 'CANBK.NS',
 'CDSL.NS',
 'CESC.NS',
 'CGPOWER.NS',
 'CHAMBLFERT.NS',
 'CHOLAFIN.NS',
 'CIPLA.NS',
 'COALINDIA.NS',
 'COFORGE.NS',
 'COLPAL.NS',
 'CONCOR.NS',
 'CROMPTON.NS',
 'CUMMINSIND.NS',
 'CYIENT.NS',
 'DABUR.NS',
 'DALBHARAT.NS',
 'DEEPAKNTR.NS',
 'DELHIVERY.NS',
 'DIVISLAB.NS',
 'DIXON.NS',
 'DLF.NS',
 'DMART.NS',
 'DRREDDY.NS',
 'EICHERMOT.NS

In [16]:
# ticker = yf.Tickers(list(symbols_dict.values()))
# close = ticker.download(period = '1d')['Close']
# close
ticker = yf.Ticker('^NSEI')
close = ticker.history(period = '1d')['Close'][0]
close

24334.19921875

In [17]:
#strikes = options_df[options_df['name'] == symbols[0]]['strike'].unique()
strikes = options_df[options_df['name'] == 'NIFTY']['strike'].unique()
strikes

array([24350., 24300., 24400., 24250., 24450., 24200., 24500., 24150.,
       24550., 24100., 24600., 24050., 24650., 24000., 24700., 24750.,
       26100., 26050., 26000., 25950., 25900., 25850., 25800., 25750.,
       25700., 25650., 25600., 25550., 25500., 25450., 25400., 25350.,
       25300., 25250., 25200., 25150., 25100., 25050., 25000., 24950.,
       24900., 24850., 24800., 23950., 23900., 23850., 23800., 23750.,
       23700., 23650., 23600., 23550., 23500., 23450., 23400., 23350.,
       23300., 23250., 23200., 23150., 23100., 23050., 23000., 22950.,
       22900., 22850., 22800., 22750., 22700., 22650., 22600., 22550.,
       22500., 22450., 22400., 22350., 22300., 22250., 22200., 22150.,
       22100., 22050., 22000., 21950., 21900., 21850., 21800., 21750.,
       21700., 21650., 21600., 21550., 21500., 21450., 21400., 21350.,
       21300., 21250., 21200., 21150., 21100., 21050., 21000., 20950.,
       20900., 20850., 20800., 20750., 20700., 20650., 20600., 20550.,
      

In [36]:
#close[symbols_dict[symbols[0]]][0]

24335.80078125

In [18]:
#cmp = close[symbols_dict[symbols[0]]][0]
cmp = close
# Sort strikes based on absolute distance from CMP
top_5_atm_strikes = sorted(strikes, key=lambda x: abs(x - cmp))[:5]
top_5_atm_strikes

[24350.0, 24300.0, 24400.0, 24250.0, 24450.0]

In [19]:
options_df[(options_df['name']==symbols[0])&(options_df['strike'].isin(top_5_atm_strikes))&
           (pd.to_datetime(options_df['expiry']) > today)]

instrument_token exchange_token      tradingsymbol   name  last_price  \
653            9882626          38604  NIFTY2550824350CE  NIFTY         0.0   
654            9882882          38605  NIFTY2550824350PE  NIFTY         0.0   
655            9882114          38602  NIFTY2550824300CE  NIFTY         0.0   
656            9882370          38603  NIFTY2550824300PE  NIFTY         0.0   
657            9883138          38606  NIFTY2550824400CE  NIFTY         0.0   
658            9883394          38607  NIFTY2550824400PE  NIFTY         0.0   
659            9881602          38600  NIFTY2550824250CE  NIFTY         0.0   
660            9881858          38601  NIFTY2550824250PE  NIFTY         0.0   
661            9883650          38608  NIFTY2550824450CE  NIFTY         0.0   
662            9883906          38609  NIFTY2550824450PE  NIFTY         0.0   
883           11843586          46264  NIFTY2551524350CE  NIFTY         0.0   
884           11843842          46265  NIFTY2551524350PE  NIFTY         0.0   
885           11843074          46262  NIFTY2551524300CE  NIFTY         0.0   
886           11843330          46263  NIFTY2551524300PE  NIFTY         0.0   
887           11844098          46266  NIFTY2551524400CE  NIFTY         0.0   
888           11844354          46267  NIFTY2551524400PE  NIFTY         0.0   
889           11842562          46260  NIFTY2551524250CE  NIFTY         0.0   
890           11842818          46261  NIFTY2551524250PE  NIFTY         0.0   
891           11844610          46268  NIFTY2551524450CE  NIFTY         0.0   
892           11844866          46269  NIFTY2551524450PE  NIFTY         0.0   
1103          12594690          49198  NIFTY2552224350CE  NIFTY         0.0   
1104          12595458          49201  NIFTY2552224350PE  NIFTY         0.0   
1105          12594178          49196  NIFTY2552224300CE  NIFTY         0.0   
1106          12594434          49197  NIFTY2552224300PE  NIFTY         0.0   
1107          12595714          49202  NIFTY2552224400CE  NIFTY         0.0   
1108          12595970          49203  NIFTY2552224400PE  NIFTY         0.0   
1109          12593666          49194  NIFTY2552224250CE  NIFTY         0.0   
1110          12593922          49195  NIFTY2552224250PE  NIFTY         0.0   
1111          12596226          49204  NIFTY2552224450CE  NIFTY         0.0   
1112          12596482          49205  NIFTY2552224450PE  NIFTY         0.0   
1265          15789314          61677  NIFTY25MAY24350CE  NIFTY         0.0   
1266          15789570          61678  NIFTY25MAY24350PE  NIFTY         0.0   
1267          15788802          61675  NIFTY25MAY24300CE  NIFTY         0.0   
1268          15789058          61676  NIFTY25MAY24300PE  NIFTY         0.0   
1269          15789826          61679  NIFTY25MAY24400CE  NIFTY         0.0   
1270          15790082          61680  NIFTY25MAY24400PE  NIFTY         0.0   
1271          15788290          61673  NIFTY25MAY24250CE  NIFTY         0.0   
1272          15788546          61674  NIFTY25MAY24250PE  NIFTY         0.0   
1273          15790338          61681  NIFTY25MAY24450CE  NIFTY         0.0   
1274          15790594          61682  NIFTY25MAY24450PE  NIFTY         0.0   
1563          10354946          40449  NIFTY2560524250CE  NIFTY         0.0   
1564          10355202          40450  NIFTY2560524250PE  NIFTY         0.0   
1565          10355458          40451  NIFTY2560524300CE  NIFTY         0.0   
1566          10355714          40452  NIFTY2560524300PE  NIFTY         0.0   
1567          10356994          40457  NIFTY2560524350CE  NIFTY         0.0   
1568          10357250          40458  NIFTY2560524350PE  NIFTY         0.0   
1569          10357506          40459  NIFTY2560524400CE  NIFTY         0.0   
1570          10357762          40460  NIFTY2560524400PE  NIFTY         0.0   
1571          10359042          40465  NIFTY2560524450CE  NIFTY         0.0   
1572          10359298          40466  NIFTY2560524450PE

In [21]:
options_df_temp = options_df[(options_df['name']=='NIFTY')&(options_df['strike'].isin(top_5_atm_strikes))&
           (pd.to_datetime(options_df['expiry']) > today)]
ce = options_df_temp[options_df_temp['instrument_type']=='CE']
pe = options_df_temp[options_df_temp['instrument_type']=='PE']
it_ce = list(ce['instrument_token'])
it_pe = list(pe['instrument_token'])
quotes = init_zerodha.kite.quote([it_ce, it_pe])

In [38]:
quotes['9882882']

{'instrument_token': 9882882,
 'timestamp': datetime.datetime(1970, 1, 1, 5, 30),
 'last_trade_time': datetime.datetime(2025, 4, 30, 15, 29, 59),
 'last_price': 233.9,
 'last_quantity': 75,
 'buy_quantity': 0,
 'sell_quantity': 0,
 'volume': 0,
 'average_price': 0,
 'oi': 1114200,
 'oi_day_high': 0,
 'oi_day_low': 0,
 'net_change': 0,
 'lower_circuit_limit': 0.05,
 'upper_circuit_limit': 547.75,
 'ohlc': {'open': 221.7, 'high': 274.05, 'low': 204.15, 'close': 233.9},
 'depth': {'buy': [{'price': 0, 'quantity': 0, 'orders': 0},
   {'price': 0, 'quantity': 0, 'orders': 0},
   {'price': 0, 'quantity': 0, 'orders': 0},
   {'price': 0, 'quantity': 0, 'orders': 0},
   {'price': 0, 'quantity': 0, 'orders': 0}],
  'sell': [{'price': 0, 'quantity': 0, 'orders': 0},
   {'price': 0, 'quantity': 0, 'orders': 0},
   {'price': 0, 'quantity': 0, 'orders': 0},
   {'price': 0, 'quantity': 0, 'orders': 0},
   {'price': 0, 'quantity': 0, 'orders': 0}]}}

In [44]:
quotes['9882626']

{'instrument_token': 9882626,
 'timestamp': datetime.datetime(1970, 1, 1, 5, 30),
 'last_trade_time': datetime.datetime(2025, 4, 30, 15, 29, 59),
 'last_price': 235.4,
 'last_quantity': 75,
 'buy_quantity': 0,
 'sell_quantity': 0,
 'volume': 0,
 'average_price': 0,
 'oi': 951675,
 'oi_day_high': 0,
 'oi_day_low': 0,
 'net_change': 0,
 'lower_circuit_limit': 0.05,
 'upper_circuit_limit': 568.1,
 'ohlc': {'open': 226.5, 'high': 262.1, 'low': 183.65, 'close': 235.4},
 'depth': {'buy': [{'price': 0, 'quantity': 0, 'orders': 0},
   {'price': 0, 'quantity': 0, 'orders': 0},
   {'price': 0, 'quantity': 0, 'orders': 0},
   {'price': 0, 'quantity': 0, 'orders': 0},
   {'price': 0, 'quantity': 0, 'orders': 0}],
  'sell': [{'price': 0, 'quantity': 0, 'orders': 0},
   {'price': 0, 'quantity': 0, 'orders': 0},
   {'price': 0, 'quantity': 0, 'orders': 0},
   {'price': 0, 'quantity': 0, 'orders': 0},
   {'price': 0, 'quantity': 0, 'orders': 0}]}}

In [52]:
ce[ce['instrument_token']==9882626]['expiry'].values[0]

datetime.date(2025, 5, 8)

In [29]:
list(pe[pe['strike']==top_5_atm_strikes[0]]['instrument_token'])

[9882882, 11843842, 12595458, 15789570, 10357250, 15966722]

In [32]:
pe_q = quotes['9882882']

In [39]:
it = list(pe[pe['strike']==top_5_atm_strikes[0]]['instrument_token'])
pe_q = {i : quotes[str(i)] for i in it}
pe_q

{9882882: {'instrument_token': 9882882,
  'timestamp': datetime.datetime(1970, 1, 1, 5, 30),
  'last_trade_time': datetime.datetime(2025, 4, 30, 15, 29, 59),
  'last_price': 233.9,
  'last_quantity': 75,
  'buy_quantity': 0,
  'sell_quantity': 0,
  'volume': 0,
  'average_price': 0,
  'oi': 1114200,
  'oi_day_high': 0,
  'oi_day_low': 0,
  'net_change': 0,
  'lower_circuit_limit': 0.05,
  'upper_circuit_limit': 547.75,
  'ohlc': {'open': 221.7, 'high': 274.05, 'low': 204.15, 'close': 233.9},
  'depth': {'buy': [{'price': 0, 'quantity': 0, 'orders': 0},
    {'price': 0, 'quantity': 0, 'orders': 0},
    {'price': 0, 'quantity': 0, 'orders': 0},
    {'price': 0, 'quantity': 0, 'orders': 0},
    {'price': 0, 'quantity': 0, 'orders': 0}],
   'sell': [{'price': 0, 'quantity': 0, 'orders': 0},
    {'price': 0, 'quantity': 0, 'orders': 0},
    {'price': 0, 'quantity': 0, 'orders': 0},
    {'price': 0, 'quantity': 0, 'orders': 0},
    {'price': 0, 'quantity': 0, 'orders': 0}]}},
 11843842: {'in

In [71]:
ce_chain = pd.DataFrame(columns = ['symbol', 'strike', 'expiry', 'ce_bid_qty', 'ce_bid_price', 'ce_ask_price', 'ce_ask_qty',
                                  'ce_oi', 'ce_inst_token', 'ce_open', 'ce_high', 'ce_low', 'ce_close' ])
pe_chain = pd.DataFrame(columns = ['symbol', 'strike', 'expiry', 'pe_bid_qty', 'pe_bid_price', 'pe_ask_price', 'pe_ask_qty',
                                  'pe_oi', 'pe_inst_token', 'pe_open', 'pe_high', 'pe_low', 'pe_close' ])


    # for each ATM strike, build one JSON object with both CE & PE data
for strike in top_5_atm_strikes:
    ce_df = ce[ce['strike'] == strike]
    it = list(ce[ce['strike']==strike]['instrument_token'])
    ce_q = {i : quotes[str(i)] for i in it}
    pe_df = pe[pe['strike'] == strike]
    it = list(pe[pe['strike']==strike]['instrument_token'])
    pe_q = {i : quotes[str(i)] for i in it}
    
    for k in ce_q.keys():
        temp_dict = quotes[str(k)]
        
        new_row = {'symbol' : 'NIFTY', 'strike' : strike, 
                   'expiry' : ce_df[ce_df['instrument_token']==int(k)]['expiry'].values[0] , 
                   'ce_bid_qty' : temp_dict['depth']['buy'][0]['quantity'], 
                   'ce_bid_price': temp_dict['depth']['buy'][0]['price'], 
                   'ce_ask_price' : temp_dict['depth']['sell'][0]['price'], 
                   'ce_ask_qty':temp_dict['depth']['sell'][0]['quantity'],
                    'ce_oi' : temp_dict['oi'] , 
                   'ce_inst_token' : k, 'ce_open':temp_dict['ohlc']['open'], 
                   'ce_high':temp_dict['ohlc']['high'], 'ce_low':temp_dict['ohlc']['low'], 
                   'ce_close':temp_dict['ohlc']['close']}
        ce_chain.loc[len(ce_chain)] = new_row
    
    for k in pe_q.keys():
        temp_dict = quotes[str(k)]
        
        new_row = {'symbol' : 'NIFTY', 'strike' : strike, 
                   'expiry' : pe_df[pe_df['instrument_token']==int(k)]['expiry'].values[0] , 
                   'pe_bid_qty' : temp_dict['depth']['buy'][0]['quantity'], 
                   'pe_bid_price': temp_dict['depth']['buy'][0]['price'], 
                   'pe_ask_price' : temp_dict['depth']['sell'][0]['price'], 
                   'pe_ask_qty':temp_dict['depth']['sell'][0]['quantity'],
                    'pe_oi' : temp_dict['oi'] , 
                   'pe_inst_token' : k, 'pe_open':temp_dict['ohlc']['open'], 
                   'pe_high':temp_dict['ohlc']['high'], 'pe_low':temp_dict['ohlc']['low'], 
                   'pe_close':temp_dict['ohlc']['close']}
        pe_chain.loc[len(pe_chain)] = new_row
    
    
    final_df = pd.merge(ce_chain, pe_chain, on = ['symbol', 'strike', 'expiry'], how = 'left') 

In [74]:
final_df

symbol   strike      expiry  ce_bid_qty  ce_bid_price  ce_ask_price  \
0   NIFTY  24350.0  2025-05-08           0             0             0   
1   NIFTY  24350.0  2025-05-15           0             0             0   
2   NIFTY  24350.0  2025-05-22           0             0             0   
3   NIFTY  24350.0  2025-05-29           0             0             0   
4   NIFTY  24350.0  2025-06-05           0             0             0   
5   NIFTY  24350.0  2025-06-26           0             0             0   
6   NIFTY  24300.0  2025-05-08           0             0             0   
7   NIFTY  24300.0  2025-05-15           0             0             0   
8   NIFTY  24300.0  2025-05-22           0             0             0   
9   NIFTY  24300.0  2025-05-29           0             0             0   
10  NIFTY  24300.0  2025-06-05           0             0             0   
11  NIFTY  24300.0  2025-06-26           0             0             0   
12  NIFTY  24400.0  2025-05-08           0             0             0   
13  NIFTY  24400.0  2025-05-15           0             0             0   
14  NIFTY  24400.0  2025-05-22           0             0             0   
15  NIFTY  24400.0  2025-05-29           0             0             0   
16  NIFTY  24400.0  2025-06-05           0             0             0   
17  NIFTY  24400.0  2025-06-26           0             0             0   
18  NIFTY  24250.0  2025-05-08           0             0             0   
19  NIFTY  24250.0  2025-05-15           0             0             0   
20  NIFTY  24250.0  2025-05-22           0             0             0   
21  NIFTY  24250.0  2025-05-29           0             0             0   
22  NIFTY  24250.0  2025-06-05           0             0             0   
23  NIFTY  24250.0  2025-06-26           0             0             0   
24  NIFTY  24450.0  2025-05-08           0             0             0   
25  NIFTY  24450.0  2025-05-15           0             0             0   
26  NIFTY  24450.0  2025-05-22           0             0             0   
27  NIFTY  24450.0  2025-05-29           0             0             0   
28  NIFTY  24450.0  2025-06-05           0             0             0   
29  NIFTY  24450.0  2025-06-26           0             0             0   

    ce_ask_qty    ce_oi  ce_inst_token  ce_open  ...  pe_bid_qty  \
0            0   951675        9882626   226.50  ...           0   
1            0    50325       11843586   330.00  ...           0   
2            0     1500       12594690   439.25  ...           0   
3            0    95850       15789314   431.00  ...           0   
4            0   256920       10356994     2.80  ...           0   
5            0    13875       15965954   683.95  ...           0   
6            0  2247750        9882114   251.50  ...           0   
7            0   189225       11843074   329.10  ...           0   
8            0    11475       12594178   414.85  ...           0   
9            0  1082925       15788802   473.40  ...           0   
10           0        0       10355458     0.00  ...           0   
11           0    71925       15964930   730.00  ...           0   
12           0  2887725        9883138   189.95  ...           0   
13           0   309825       11844098   277.05  ...           0   
14           0     8775       12595714   395.30  ...           0   
15           0   744675       15789826   453.25  ...           0   
16           0  1661475       10357506    13.15  ...           0   
17           0    42150       15966978   641.00  ...           0   
18           0   268875        9881602   285.70  ...           0   
19           0    27075       11842562   398.00  ...           0   
20           0       75       12593666     0.00  ...           0   
21           0    79275       15788290   517.95  ...           0   
22           0  1355565       10354946     9.00  ...           0   
23           0     5925       15964418   757.20  ...           0   
24      

In [34]:
import pickle
with open("options_json_for_ui_testing_2.pkl", "rb") as file:
    symbols_json = pickle.load(file)
symbols_json

{'NIFTY': {'underlying': 'Nifty 50',
  'category': 'index',
  'realized_volatility': {'Close-to-close': date
   2024-05-24    0.111183
   2024-05-27    0.111187
   2024-05-28    0.110562
   2024-05-29    0.108837
   2024-05-30    0.107593
                   ...   
   2025-04-02    0.122269
   2025-04-03    0.122821
   2025-04-04    0.130676
   2025-04-07    0.161807
   2025-04-08    0.174610
   Name: close, Length: 218, dtype: float64,
   'Yang-Zhang': date
   2024-05-24    0.123144
   2024-05-27    0.123945
   2024-05-28    0.123617
   2024-05-29    0.123840
   2024-05-30    0.123036
                   ...   
   2025-04-02    0.126426
   2025-04-03    0.126899
   2025-04-04    0.128103
   2025-04-07    0.202202
   2025-04-08    0.209303
   Length: 218, dtype: float64,
   'Parkinson': date
   2024-05-23    0.105233
   2024-05-24    0.105008
   2024-05-27    0.105888
   2024-05-28    0.106133
   2024-05-29    0.105287
                   ...   
   2025-04-02    0.099230
   2025-04-03    

In [51]:
atm_results = []
for symbol in symbols[:4]:
    print(f"Processing: {symbol}")
    
    cmp = close[symbols_dict[symbol]][0]
    #print(cmp)
    strikes = options_df[options_df['name'] == symbol]['strike'].unique()
    #print(strikes)
    top_5_atm_strikes = sorted(strikes, key=lambda x: abs(x - cmp))[:5]
    #print(top_5_atm_strikes)
    # Filter option contracts for the symbol (nearest expiry)
    options_df_temp = options_df[(options_df['name']==symbol)&(options_df['strike'].isin(top_5_atm_strikes))&
           (pd.to_datetime(options_df['expiry']) > today)]
    #print(options_df_temp)
                
    ce = options_df_temp[options_df_temp['instrument_type']=='CE']
    pe = options_df_temp[options_df_temp['instrument_type']=='PE']
    
    it_ce = list(ce['instrument_token'])
    it_pe = list(pe['instrument_token'])
    quotes = init_zerodha.kite.quote([it_ce, it_pe])
    atm_results.append(quotes)

# Compile and Sort results
atm_oi_df = pd.DataFrame(atm_results)
print(atm_oi_df)

Processing: NIFTY
Processing: BANKNIFTY
Processing: AARTIIND
Processing: ABB
                                            11842562  \
0  {'instrument_token': 11842562, 'timestamp': 20...   
1                                                NaN   
2                                                NaN   
3                                                NaN   

                                            11842818  \
0  {'instrument_token': 11842818, 'timestamp': 20...   
1                                                NaN   
2                                                NaN   
3                                                NaN   

                                            11843074  \
0  {'instrument_token': 11843074, 'timestamp': 20...   
1                                                NaN   
2                                                NaN   
3                                                NaN   

                                            11843330  \
0  {'instrument_token': 

In [53]:
atm_results

[{'11842562': {'instrument_token': 11842562,
   'timestamp': datetime.datetime(2025, 4, 30, 15, 2, 35),
   'last_trade_time': datetime.datetime(2025, 4, 30, 15, 1, 59),
   'last_price': 421.3,
   'last_quantity': 150,
   'buy_quantity': 15525,
   'sell_quantity': 6750,
   'volume': 21825,
   'average_price': 401.89,
   'oi': 19575,
   'oi_day_high': 19650,
   'oi_day_low': 16575,
   'net_change': 0,
   'lower_circuit_limit': 23.5,
   'upper_circuit_limit': 772.7,
   'ohlc': {'open': 398, 'high': 433, 'low': 352.4, 'close': 398.1},
   'depth': {'buy': [{'price': 421.7, 'quantity': 150, 'orders': 1},
     {'price': 421.65, 'quantity': 225, 'orders': 1},
     {'price': 421.4, 'quantity': 225, 'orders': 1},
     {'price': 419.55, 'quantity': 2475, 'orders': 13},
     {'price': 419.45, 'quantity': 150, 'orders': 1}],
    'sell': [{'price': 428.45, 'quantity': 75, 'orders': 1},
     {'price': 428.5, 'quantity': 225, 'orders': 1},
     {'price': 430.95, 'quantity': 750, 'orders': 1},
     {'p